# MUC16 Mutation Trans Effect on Phosphoproteomics

This notebook analyzes the trans effect of MUC16 mutation on interacting and other proteins Phosphoproteomics, in Endometrial, Colon, and Ovarian cancer.

### Library Imports

In [1]:
import pandas as pd
import numpy as np
import scipy.stats
import collections
import re
import gseapy as gp
from gseapy.plot import barplot, dotplot
import matplotlib.pyplot as plt
import seaborn as sns

import cptac
import cptac.algorithms as al

en = cptac.Endometrial()
co = cptac.Colon()
ov = cptac.Ovarian()

### Investigate MUC16 gene

In [2]:
gene = "MUC16"

### Investigate Proteomics, Phosphoproteomics, Acetylproteomics, or Transcriptomics

In [3]:
#omics = "proteomics"
#omics = "transcriptomics"
omics = "phosphoproteomics"
#omics = "acetylproteomics"

# Interacting Proteins: Transcriptomics

## Endometrial

### Generate interacting protein list

In [10]:
'''Use get interacting proteins method to generate list of interacting proteins'''
interacting_proteins = al.get_interacting_proteins(gene)

omics_object = en.get_phosphoproteomics()

print("Generating interacting protein list")
interacting_proteins_in_omics_df = []

'''Only do comparisons on proteins in the omics dataframe'''
for ip in interacting_proteins:
    if omics == 'phosphoproteomics' or omics == 'acetylproteomics':
        col_regex = ip + "-.*" # Build a regex to get all columns that match the gene
    else:
        col_regex = '^{}$'.format(ip)

    selected = omics_object.filter(regex=col_regex)

    if len(selected.columns) > 0:
        interacting_proteins_in_omics_df.append(ip)

print("Interacting Proteins:")
for interacting_protein in interacting_proteins_in_omics_df:
    print(interacting_protein)

Generating interacting protein list
Interacting Proteins:
ST3GAL3
MUC16
MSLN
GALNT4
MUC5B
MUC1
MUC13
MUC5AC
LGALS1
RAD21
MCM2
EGFR
TRIM25


### Test for significant comparisons in any of interacting proteins

In [11]:
'''Create dataframe in order to do comparisons with wrap_ttest'''
protdf = en.join_omics_to_mutations(mutations_genes=[gene], omics_df_name=omics, omics_genes=interacting_proteins_in_omics_df)
protdf = protdf.loc[protdf['Sample_Status'] == 'Tumor']

'''Create the binary valued column needed to do the comparison'''
for ind, row in protdf.iterrows():
    if row[gene+"_Mutation_Status"] != 'Wildtype_Tumor':
        protdf.at[ind,'Label'] = 'Mutated'
    else:
        protdf.at[ind,'Label'] = 'Wildtype'

'''Format the dataframe correctly'''
protdf = protdf.drop(gene+"_Mutation",axis=1)
protdf = protdf.drop(gene+"_Location",axis=1)
protdf = protdf.drop(gene+"_Mutation_Status", axis=1)
protdf = protdf.drop("Sample_Status",axis=1)


'''Make list of columns to be compared using t-tests'''
col_list = list(protdf.columns)
col_list.remove('Label')

print("Doing t-test comparisons\n")

'''Call wrap_ttest, pass in formatted dataframe'''
wrap_results = al.wrap_ttest(protdf, 'Label', col_list)

'''Print results, if anything significant was found'''
if wrap_results is not None:
        print(wrap_results)
        print("\n\n")

GALNT4 did not match any columns in phosphoproteomics dataframe. GALNT4_phosphoproteomics column inserted, but filled with NaN.
Doing t-test comparisons



/anaconda3/lib/python3.6/site-packages/numpy/core/fromnumeric.py:3157: RuntimeWarning: Degrees of freedom <= 0 for slice
  **kwargs)
/anaconda3/lib/python3.6/site-packages/numpy/core/_methods.py:132: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


No significant comparisons.


## Colon

### Generate interacting protein list

In [15]:
'''Use get interacting proteins method to generate list of interacting proteins'''
interacting_proteins = al.get_interacting_proteins(gene)

omics_object = co.get_phosphoproteomics()

print("Generating interacting protein list")
interacting_proteins_in_omics_df = []

'''Only do comparisons on proteins in the omics dataframe'''
for ip in interacting_proteins:
    if omics == 'phosphoproteomics' or omics == 'acetylproteomics':
        col_regex = ip + "_.*" # Build a regex to get all columns that match the gene
    else:
        col_regex = '^{}$'.format(ip)

    selected = omics_object.filter(regex=col_regex)

    if len(selected.columns) > 0:
        interacting_proteins_in_omics_df.append(ip)

print("Interacting Proteins:")
for interacting_protein in interacting_proteins_in_omics_df:
    print(interacting_protein)

Generating interacting protein list
Interacting Proteins:
GALNT4
MUC12
MUC1
MUC13
LGALS1
RAD21
MCM2
EGFR
TRIM25


### Test for significant comparisons in any of interacting proteins

In [16]:
'''Create dataframe in order to do comparisons with wrap_ttest'''
protdf = co.join_omics_to_mutations(mutations_genes=[gene], omics_df_name=omics, omics_genes=interacting_proteins_in_omics_df)
protdf = protdf.loc[protdf['Sample_Status'] == 'Tumor']

'''Create the binary valued column needed to do the comparison'''
for ind, row in protdf.iterrows():
    if row[gene+"_Mutation_Status"] != 'Wildtype_Tumor':
        protdf.at[ind,'Label'] = 'Mutated'
    else:
        protdf.at[ind,'Label'] = 'Wildtype'

'''Format the dataframe correctly'''
protdf = protdf.drop(gene+"_Mutation",axis=1)
protdf = protdf.drop(gene+"_Location",axis=1)
protdf = protdf.drop(gene+"_Mutation_Status", axis=1)
protdf = protdf.drop("Sample_Status",axis=1)

'''Make list of columns to be compared using t-tests'''
col_list = list(protdf.columns)
col_list.remove('Label')

print("Doing t-test comparisons\n")

'''Call wrap_ttest, pass in formatted dataframe'''
wrap_results = al.wrap_ttest(protdf, 'Label', col_list)

'''Print results, if anything significant was found'''
if wrap_results is not None:
        print(wrap_results)
        print("\n\n")

GALNT4 did not match any columns in phosphoproteomics dataframe. GALNT4_phosphoproteomics column inserted, but filled with NaN.
MUC12 did not match any columns in phosphoproteomics dataframe. MUC12_phosphoproteomics column inserted, but filled with NaN.
MUC1 did not match any columns in phosphoproteomics dataframe. MUC1_phosphoproteomics column inserted, but filled with NaN.
MUC13 did not match any columns in phosphoproteomics dataframe. MUC13_phosphoproteomics column inserted, but filled with NaN.
LGALS1 did not match any columns in phosphoproteomics dataframe. LGALS1_phosphoproteomics column inserted, but filled with NaN.
RAD21 did not match any columns in phosphoproteomics dataframe. RAD21_phosphoproteomics column inserted, but filled with NaN.
MCM2 did not match any columns in phosphoproteomics dataframe. MCM2_phosphoproteomics column inserted, but filled with NaN.
EGFR did not match any columns in phosphoproteomics dataframe. EGFR_phosphoproteomics column inserted, but filled with

## Ovarian

### Generate interacting protein list

In [18]:
'''Use get interacting proteins method to generate list of interacting proteins'''
interacting_proteins = al.get_interacting_proteins(gene)

omics_object = ov.get_phosphoproteomics()

print("Generating interacting protein list")
interacting_proteins_in_omics_df = []

'''Only do comparisons on proteins in the omics dataframe'''
for ip in interacting_proteins:
    if omics == 'phosphoproteomics' or omics == 'acetylproteomics':
        col_regex = ip + "-.*" # Build a regex to get all columns that match the gene
    else:
        col_regex = '^{}$'.format(ip)

    selected = omics_object.filter(regex=col_regex)

    if len(selected.columns) > 0:
        interacting_proteins_in_omics_df.append(ip)

print("Interacting Proteins:")
for interacting_protein in interacting_proteins_in_omics_df:
    print(interacting_protein)

Generating interacting protein list
Interacting Proteins:
MUC21
MUC3A
MUC16
MSLN
C1GALT1
GALNT4
MUC5B
MUC1
LGALS1
UBC
RAD21
MCM2
EGFR
TRIM25


In [27]:
'''Create dataframe in order to do comparisons with wrap_ttest'''
protdf = ov.join_omics_to_mutations(mutations_genes=[gene], omics_df_name=omics, omics_genes=interacting_proteins_in_omics_df) 
protdf = protdf.loc[protdf['Sample_Status'] == 'Tumor']

'''Create the binary valued column needed to do the comparison'''
for ind, row in protdf.iterrows():
    if row[gene+"_Mutation_Status"] != 'Wildtype_Tumor':
        protdf.loc[ind,'Label'] = 'Mutated'
    else:
        protdf.loc[ind,'Label'] = 'Wildtype'

'''Format the dataframe correctly'''
protdf = protdf.drop(gene+"_Mutation",axis=1)
protdf = protdf.drop(gene+"_Location",axis=1)
protdf = protdf.drop(gene+"_Mutation_Status", axis=1)
protdf = protdf.drop("Sample_Status",axis=1)
protdf = protdf.loc[:,~protdf.columns.duplicated()]

'''Make list of columns to be compared using t-tests'''
col_list = list(protdf.columns)
col_list.remove('Label')

print("Doing t-test comparisons\n")

'''Call wrap_ttest, pass in formatted dataframe'''
wrap_results = al.wrap_ttest(protdf, 'Label', col_list)

'''Print results, if anything significant was found'''
if wrap_results is not None:
        print(wrap_results)
        print("\n\n")

GALNT4 did not match any columns in phosphoproteomics dataframe. GALNT4_phosphoproteomics column inserted, but filled with NaN.
Doing t-test comparisons

No significant comparisons.


# All Proteins: Transcriptomics

## Endometrial

In [ ]:
try:
    print("\nGene: ", gene)

    '''Use all proteins'''
    proteomics = en.get_phosphoproteomics()
    all_proteins = proteomics.columns
    #all_proteins = all_proteins[:100]

    '''Create dataframe in order to do comparisons with wrap_ttest'''
    protdf = en.join_omics_to_mutations(mutations_genes=[gene], omics_df_name=omics, omics_genes=all_proteins)
    protdf = protdf.loc[protdf['Sample_Status'] == 'Tumor']
    
    '''Create the binary valued column needed to do the comparison'''
    for ind, row in protdf.iterrows():
        if row[gene+"_Mutation_Status"] != 'Wildtype_Tumor':
            protdf.at[ind,'Label'] = 'Mutated'
        else:
            protdf.at[ind,'Label'] = 'Wildtype'

    '''Format the datafram correctly'''
    protdf = protdf.drop(gene+"_Mutation",axis=1)
    protdf = protdf.drop(gene+"_Location",axis=1)
    protdf = protdf.drop(gene+"_Mutation_Status", axis=1)
    protdf = protdf.drop("Sample_Status",axis=1)

    '''Make list of columns to be compared using t-tests'''
    col_list = list(protdf.columns)
    col_list.remove('Label')

    print("Doing t-test comparisons\n")
    
    '''Call wrap_ttest, pass in formatted dataframe'''
    wrap_results = al.wrap_ttest(protdf, 'Label', col_list)

    '''Print results, if anything significant was found'''
    if wrap_results is not None:
            print(wrap_results)
            print("\n\n")

except Exception as e:
    print("Error in Comparison")
    print(e)


Gene:  MUC16
AAAS-S495 did not match any columns in phosphoproteomics dataframe. AAAS-S495_phosphoproteomics column inserted, but filled with NaN.
AAAS-S541 did not match any columns in phosphoproteomics dataframe. AAAS-S541_phosphoproteomics column inserted, but filled with NaN.
AAAS-Y485 did not match any columns in phosphoproteomics dataframe. AAAS-Y485_phosphoproteomics column inserted, but filled with NaN.
AACS-S618 did not match any columns in phosphoproteomics dataframe. AACS-S618_phosphoproteomics column inserted, but filled with NaN.
AAED1-S12 did not match any columns in phosphoproteomics dataframe. AAED1-S12_phosphoproteomics column inserted, but filled with NaN.
AAGAB-S310 did not match any columns in phosphoproteomics dataframe. AAGAB-S310_phosphoproteomics column inserted, but filled with NaN.
AAGAB-S311 did not match any columns in phosphoproteomics dataframe. AAGAB-S311_phosphoproteomics column inserted, but filled with NaN.
AAK1-S14 did not match any columns in phosph

ABCA1-S1296 did not match any columns in phosphoproteomics dataframe. ABCA1-S1296_phosphoproteomics column inserted, but filled with NaN.
ABCA1-S884 did not match any columns in phosphoproteomics dataframe. ABCA1-S884_phosphoproteomics column inserted, but filled with NaN.
ABCA13-S318 did not match any columns in phosphoproteomics dataframe. ABCA13-S318_phosphoproteomics column inserted, but filled with NaN.
ABCA13-T317 did not match any columns in phosphoproteomics dataframe. ABCA13-T317_phosphoproteomics column inserted, but filled with NaN.
ABCA2-S1358 did not match any columns in phosphoproteomics dataframe. ABCA2-S1358_phosphoproteomics column inserted, but filled with NaN.
ABCA2-S1362 did not match any columns in phosphoproteomics dataframe. ABCA2-S1362_phosphoproteomics column inserted, but filled with NaN.
ABCA2-S1399 did not match any columns in phosphoproteomics dataframe. ABCA2-S1399_phosphoproteomics column inserted, but filled with NaN.
ABCA2-S1402 did not match any column

ABCF1-S228 did not match any columns in phosphoproteomics dataframe. ABCF1-S228_phosphoproteomics column inserted, but filled with NaN.
ABCF1-S244 did not match any columns in phosphoproteomics dataframe. ABCF1-S244_phosphoproteomics column inserted, but filled with NaN.
ABCF1-S254 did not match any columns in phosphoproteomics dataframe. ABCF1-S254_phosphoproteomics column inserted, but filled with NaN.
ABCF1-S595 did not match any columns in phosphoproteomics dataframe. ABCF1-S595_phosphoproteomics column inserted, but filled with NaN.
ABCF1-S621 did not match any columns in phosphoproteomics dataframe. ABCF1-S621_phosphoproteomics column inserted, but filled with NaN.
ABCF1-T108 did not match any columns in phosphoproteomics dataframe. ABCF1-T108_phosphoproteomics column inserted, but filled with NaN.
ABCF1-T21 did not match any columns in phosphoproteomics dataframe. ABCF1-T21_phosphoproteomics column inserted, but filled with NaN.
ABCF2-S349 did not match any columns in phosphopro

ABI3-S213 did not match any columns in phosphoproteomics dataframe. ABI3-S213_phosphoproteomics column inserted, but filled with NaN.
ABI3-S216 did not match any columns in phosphoproteomics dataframe. ABI3-S216_phosphoproteomics column inserted, but filled with NaN.
ABI3-S342 did not match any columns in phosphoproteomics dataframe. ABI3-S342_phosphoproteomics column inserted, but filled with NaN.
ABI3-T134 did not match any columns in phosphoproteomics dataframe. ABI3-T134_phosphoproteomics column inserted, but filled with NaN.
ABI3-Y361 did not match any columns in phosphoproteomics dataframe. ABI3-Y361_phosphoproteomics column inserted, but filled with NaN.
ABI3BP-S1419 did not match any columns in phosphoproteomics dataframe. ABI3BP-S1419_phosphoproteomics column inserted, but filled with NaN.
ABI3BP-T1396 did not match any columns in phosphoproteomics dataframe. ABI3BP-T1396_phosphoproteomics column inserted, but filled with NaN.
ABL1-S16 did not match any columns in phosphoprote

ABLIM1-S363 did not match any columns in phosphoproteomics dataframe. ABLIM1-S363_phosphoproteomics column inserted, but filled with NaN.
ABLIM1-S367 did not match any columns in phosphoproteomics dataframe. ABLIM1-S367_phosphoproteomics column inserted, but filled with NaN.
ABLIM1-S422 did not match any columns in phosphoproteomics dataframe. ABLIM1-S422_phosphoproteomics column inserted, but filled with NaN.
ABLIM1-S426 did not match any columns in phosphoproteomics dataframe. ABLIM1-S426_phosphoproteomics column inserted, but filled with NaN.
ABLIM1-S431 did not match any columns in phosphoproteomics dataframe. ABLIM1-S431_phosphoproteomics column inserted, but filled with NaN.
ABLIM1-S435 did not match any columns in phosphoproteomics dataframe. ABLIM1-S435_phosphoproteomics column inserted, but filled with NaN.
ABLIM1-S450 did not match any columns in phosphoproteomics dataframe. ABLIM1-S450_phosphoproteomics column inserted, but filled with NaN.
ABLIM1-S452 did not match any colu

...

SYNPO2-S212 did not match any columns in phosphoproteomics dataframe. SYNPO2-S212_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-S224 did not match any columns in phosphoproteomics dataframe. SYNPO2-S224_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-S226 did not match any columns in phosphoproteomics dataframe. SYNPO2-S226_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-S234 did not match any columns in phosphoproteomics dataframe. SYNPO2-S234_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-S243 did not match any columns in phosphoproteomics dataframe. SYNPO2-S243_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-S257 did not match any columns in phosphoproteomics dataframe. SYNPO2-S257_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-S263 did not match any columns in phosphoproteomics dataframe. SYNPO2-S263_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-S274 did not match any colu

SYNPO2-S930 did not match any columns in phosphoproteomics dataframe. SYNPO2-S930_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-S940 did not match any columns in phosphoproteomics dataframe. SYNPO2-S940_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-S943 did not match any columns in phosphoproteomics dataframe. SYNPO2-S943_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-S97 did not match any columns in phosphoproteomics dataframe. SYNPO2-S97_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-S998 did not match any columns in phosphoproteomics dataframe. SYNPO2-S998_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-T1202 did not match any columns in phosphoproteomics dataframe. SYNPO2-T1202_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-T1209 did not match any columns in phosphoproteomics dataframe. SYNPO2-T1209_phosphoproteomics column inserted, but filled with NaN.
SYNPO2-T1210 did not match any c

SYNRG-S497 did not match any columns in phosphoproteomics dataframe. SYNRG-S497_phosphoproteomics column inserted, but filled with NaN.
SYNRG-S580 did not match any columns in phosphoproteomics dataframe. SYNRG-S580_phosphoproteomics column inserted, but filled with NaN.
SYNRG-S642 did not match any columns in phosphoproteomics dataframe. SYNRG-S642_phosphoproteomics column inserted, but filled with NaN.
SYNRG-S651 did not match any columns in phosphoproteomics dataframe. SYNRG-S651_phosphoproteomics column inserted, but filled with NaN.
SYNRG-S720 did not match any columns in phosphoproteomics dataframe. SYNRG-S720_phosphoproteomics column inserted, but filled with NaN.
SYNRG-S730 did not match any columns in phosphoproteomics dataframe. SYNRG-S730_phosphoproteomics column inserted, but filled with NaN.
SYNRG-S752 did not match any columns in phosphoproteomics dataframe. SYNRG-S752_phosphoproteomics column inserted, but filled with NaN.
SYNRG-S756 did not match any columns in phosphop

SYTL1-S441 did not match any columns in phosphoproteomics dataframe. SYTL1-S441_phosphoproteomics column inserted, but filled with NaN.
SYTL1-S470 did not match any columns in phosphoproteomics dataframe. SYTL1-S470_phosphoproteomics column inserted, but filled with NaN.
SYTL1-S69 did not match any columns in phosphoproteomics dataframe. SYTL1-S69_phosphoproteomics column inserted, but filled with NaN.
SYTL1-T249 did not match any columns in phosphoproteomics dataframe. SYTL1-T249_phosphoproteomics column inserted, but filled with NaN.
SYTL2-S154 did not match any columns in phosphoproteomics dataframe. SYTL2-S154_phosphoproteomics column inserted, but filled with NaN.
SYTL2-S278 did not match any columns in phosphoproteomics dataframe. SYTL2-S278_phosphoproteomics column inserted, but filled with NaN.
SYTL2-S279 did not match any columns in phosphoproteomics dataframe. SYTL2-S279_phosphoproteomics column inserted, but filled with NaN.
SYTL2-S302 did not match any columns in phosphopro

SZRD1-T121 did not match any columns in phosphoproteomics dataframe. SZRD1-T121_phosphoproteomics column inserted, but filled with NaN.
SZRD1-T67 did not match any columns in phosphoproteomics dataframe. SZRD1-T67_phosphoproteomics column inserted, but filled with NaN.
SZRD1-T78 did not match any columns in phosphoproteomics dataframe. SZRD1-T78_phosphoproteomics column inserted, but filled with NaN.
SZRD1-T82 did not match any columns in phosphoproteomics dataframe. SZRD1-T82_phosphoproteomics column inserted, but filled with NaN.
SZT2-S1152 did not match any columns in phosphoproteomics dataframe. SZT2-S1152_phosphoproteomics column inserted, but filled with NaN.
SZT2-S1168 did not match any columns in phosphoproteomics dataframe. SZT2-S1168_phosphoproteomics column inserted, but filled with NaN.
SZT2-S1219 did not match any columns in phosphoproteomics dataframe. SZT2-S1219_phosphoproteomics column inserted, but filled with NaN.
SZT2-S1329 did not match any columns in phosphoproteom

## Colon

In [ ]:
try:
    print("\nGene: ", gene)

    '''Use all proteins'''
    proteomics = co.get_phosphoproteomics()
    all_proteins = proteomics.columns
    #all_proteins = all_proteins[:100]

    '''Create dataframe in order to do comparisons with wrap_ttest'''
    protdf = co.join_omics_to_mutations(mutations_genes=[gene], omics_df_name=omics, omics_genes=all_proteins)
    protdf = protdf.loc[protdf['Sample_Status'] == 'Tumor']
    
    '''Create the binary valued column needed to do the comparison'''
    for ind, row in protdf.iterrows():
        if row[gene+"_Mutation_Status"] != 'Wildtype_Tumor':
            protdf.at[ind,'Label'] = 'Mutated'
        else:
            protdf.at[ind,'Label'] = 'Wildtype'

    '''Format the datafram correctly'''
    protdf = protdf.drop(gene+"_Mutation",axis=1)
    protdf = protdf.drop(gene+"_Location",axis=1)
    protdf = protdf.drop(gene+"_Mutation_Status", axis=1)
    protdf = protdf.drop("Sample_Status",axis=1)

    '''Make list of columns to be compared using t-tests'''
    col_list = list(protdf.columns)
    col_list.remove('Label')

    print("Doing t-test comparisons\n")
    
    '''Call wrap_ttest, pass in formatted dataframe'''
    wrap_results = al.wrap_ttest(protdf, 'Label', col_list)

    '''Print results, if anything significant was found'''
    if wrap_results is not None:
            print(wrap_results)
            print("\n\n")

except Exception as e:
    print("Error in Comparison")
    print(e)

## Ovarian

In [ ]:

print("\nGene: ", gene)

'''Use all proteins'''
proteomics = ov.get_phosphoproteomics()
all_proteins = list(set(proteomics.columns))

'''Create dataframe in order to do comparisons with wrap_ttest'''
protdf = ov.join_omics_to_mutations(mutations_genes=[gene], omics_df_name=omics, omics_genes=all_proteins)
protdf = protdf.loc[protdf['Sample_Status'] == 'Tumor']
protdf = protdf.loc[:,~protdf.columns.duplicated()]

'''Create the binary valued column needed to do the comparison'''
for ind, row in protdf.iterrows():
    if row[gene+"_Mutation_Status"] != 'Wildtype_Tumor':
        protdf.at[ind,'Label'] = 'Mutated'
    else:
        protdf.at[ind,'Label'] = 'Wildtype'

'''Format the datafram correctly'''
protdf = protdf.drop(gene+"_Mutation",axis=1)
protdf = protdf.drop(gene+"_Location",axis=1)
protdf = protdf.drop(gene+"_Mutation_Status", axis=1)
protdf = protdf.drop("Sample_Status",axis=1)

'''Make list of columns to be compared using t-tests'''
col_list = list(protdf.columns)
col_list.remove('Label')

print("Doing t-test comparisons\n")

'''Call wrap_ttest, pass in formatted dataframe'''
wrap_results = al.wrap_ttest(protdf, 'Label', col_list)

'''Print results, if anything significant was found'''
if wrap_results is not None:
        print(wrap_results)
        print("\n\n")


## Conclusions